## April 1 - More Learning - Statistics and Naive Bayes

Mostly chapter 18 and 20 from AIMA

In [31]:
from learning import *
from notebook import *

In [32]:
iris = DataSet(name="iris")

## NAIVE BAYES LEARNER

### Overview

#### Theory of Probabilities

The Naive Bayes algorithm is a probabilistic classifier, making use of [Bayes' Theorem](https://en.wikipedia.org/wiki/Bayes%27_theorem). The theorem states that the conditional probability of <b>A</b> given <b>B</b> equals the conditional probability of <b>B</b> given <b>A</b> multiplied by the probability of <b>A</b>, divided by the probability of <b>B</b>.

$$P(A|B) = \dfrac{P(B|A)*P(A)}{P(B)}$$

From the theory of Probabilities we have the Multiplication Rule, if the events *X* are independent the following is true:

$$P(X_{1} \cap X_{2} \cap ... \cap X_{n}) = P(X_{1})*P(X_{2})*...*P(X_{n})$$

For conditional probabilities this becomes:

$$P(X_{1}, X_{2}, ..., X_{n}|Y) = P(X_{1}|Y)*P(X_{2}|Y)*...*P(X_{n}|Y)$$

#### Classifying an Item

How can we use the above to classify an item though?

We have a dataset with a set of classes (<b>C</b>) and we want to classify an item with a set of features (<b>F</b>). Essentially what we want to do is predict the class of an item given the features.

For a specific class, <b>Class</b>, we will find the conditional probability given the item features:

$$P(Class|F) = \dfrac{P(F|Class)*P(Class)}{P(F)}$$

We will do this for every class and we will pick the maximum. This will be the class the item is classified in.

The features though are a vector with many elements. We need to break the probabilities up using the multiplication rule. Thus the above equation becomes:

$$P(Class|F) = \dfrac{P(Class)*P(F_{1}|Class)*P(F_{2}|Class)*...*P(F_{n}|Class)}{P(F_{1})*P(F_{2})*...*P(F_{n})}$$

The calculation of the conditional probability then depends on the calculation of the following:

*a)* The probability of <b>Class</b> in the dataset.

*b)* The conditional probability of each feature occurring in an item classified in <b>Class</b>.

*c)* The probabilities of each individual feature.

For *a)*, we will count how many times <b>Class</b> occurs in the dataset (aka how many items are classified in a particular class).

For *b)*, if the feature values are discrete ('Blue', '3', 'Tall', etc.), we will count how many times a feature value occurs in items of each class. If the feature values are not discrete, we will go a different route. We will use a distribution function to calculate the probability of values for a given class and feature. If we know the distribution function of the dataset, then great, we will use it to compute the probabilities. If we don't know the function, we can assume the dataset follows the normal (Gaussian) distribution without much loss of accuracy. In fact, it can be proven that any distribution tends to the Gaussian the larger the population gets (see [Central Limit Theorem](https://en.wikipedia.org/wiki/Central_limit_theorem)).

*NOTE:* If the values are continuous but use the discrete approach, there might be issues if we are not lucky. For one, if we have two values, '5.0 and 5.1', with the discrete approach they will be two completely different values, despite being so close. Second, if we are trying to classify an item with a feature value of '5.15', if the value does not appear for the feature, its probability will be 0. This might lead to misclassification. Generally, the continuous approach is more accurate and more useful, despite the overhead of calculating the distribution function.

The last one, *c)*, is tricky. If feature values are discrete, we can count how many times they occur in the dataset. But what if the feature values are continuous? Imagine a dataset with a height feature. Is it worth it to count how many times each value occurs? Most of the time it is not, since there can be miscellaneous differences in the values (for example, 1.7 meters and 1.700001 meters are practically equal, but they count as different values).

So as we cannot calculate the feature value probabilities, what are we going to do?

Let's take a step back and rethink exactly what we are doing. We are essentially comparing conditional probabilities of all the classes. For two classes, <b>A</b> and <b>B</b>, we want to know which one is greater:

$$\dfrac{P(F|A)*P(A)}{P(F)} vs. \dfrac{P(F|B)*P(B)}{P(F)}$$

Wait, <b>P(F)</b> is the same for both the classes! In fact, it is the same for every combination of classes. That is because <b>P(F)</b> does not depend on a class, thus being independent of the classes.

So, for *c)*, we actually don't need to calculate it at all.

#### Wrapping It Up

Classifying an item to a class then becomes a matter of calculating the conditional probabilities of feature values and the probabilities of classes. This is something very desirable and computationally delicious.

Remember though that all the above are true because we made the assumption that the features are independent. In most real-world cases that is not true though. Is that an issue here? Fret not, for the the algorithm is very efficient even with that assumption. That is why the algorithm is called **Naive** Bayes Classifier. We (naively) assume that the features are independent to make computations easier.

### Implementation

The implementation of the Naive Bayes Classifier is split in two; *Learning* and *Simple*. The *learning* classifier takes as input a dataset and learns the needed distributions from that. It is itself split into two, for discrete and continuous features. The *simple* classifier takes as input not a dataset, but already calculated distributions (a dictionary of `CountingProbDist` objects).

#### Discrete

The implementation for discrete values counts how many times each feature value occurs for each class, and how many times each class occurs. The results are stored in a `CountinProbDist` object.

With the below code you can see the probabilities of the class "Setosa" appearing in the dataset and the probability of the first feature (at index 0) of the same class having a value of 5. Notice that the second probability is relatively small, even though if we observe the dataset we will find that a lot of values are around 5. The issue arises because the features in the Iris dataset are continuous, and we are assuming they are discrete. If the features were discrete (for example, "Tall", "3", etc.) this probably wouldn't have been the case and we would see a much nicer probability distribution.

In [33]:
psource(CountingProbDist)

### Statistical Learning

Chapter 20, page 802

We briefly digress from the iris dataset.

There are five types of bags of candies.  Each bag has 100 pieces, individually wrapped.  One bag has all cherry (yum).
One bag has all lime (yuck).  The wrapping paper is identical and opaque.

Three other bags have a mixture: (75 cherry, 25 lime), (50 each), (25 cherry, 75 lime).

The bags themselves are not evenly distributed.  10% are all cherry and 10% are all lime.  40% are 50/50, and 20% are either 25% lime or 25% cherry.

If I give you a bag at random, you can randomly sample one candy at a time (and then rewrap it put it back in the bag).

You pick a random bag and start sampling.  If you select one lime candy, what is the most likely bag? What if you pick two in row?  Three in row? Four in a row?

We can use the CountingProbDist() to model this problem.

In [34]:
h1 = CountingProbDist('c'*100)
h2 = CountingProbDist('c'*75+'l'*25)
h3 = CountingProbDist('c'*50+'l'*50)
h4 = CountingProbDist('c'*25+'l'*75)
h5 = CountingProbDist('l'*100)
dist = {('h1', 0.1): h1, ('h2', 0.2): h2, ('h3', 0.4): h3, 
        ('h4', 0.2): h4, ('h5', 0.1): h5}
nBS = NaiveBayesLearner(dist, simple=True)

The NaiveBayesLearner is actually three functions.  Here we are using the simple one.

In [35]:
'c'*100

'cccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccc'

In [36]:
h2.dictionary

{'c': 75, 'l': 25}

In [37]:
psource(NaiveBayesLearner)

In [38]:
dir(h1)

['__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__getitem__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 'add',
 'default',
 'dictionary',
 'n_obs',
 'sample',
 'sampler',
 'smooth_for',
 'top']

In [39]:
h1.dictionary

{'c': 100}

In [40]:
h1.sample()

'c'

In [41]:
h3.dictionary

{'c': 50, 'l': 50}

In [42]:
h3.sample()

'l'

We can practice our $\LaTeX{}$

$ h1: 100\%$ cherry

$ h2: 75\%$ cherry $+ 25\%$ lime,

$ h3: 50\%$ cherry $+ 50\%$ lime,

$ h4: 25\%$ cherry $+ 75\%$ lime,

$ h5: 100\%$ lime.

$$P(h1) = 10\%$$
$$P(h2) = 20\%$$
$$P(h3) = 40\%$$
$$P(h4) = 20\%$$
$$P(h5) = 10\%$$

$$P(h_{i}|lime) = \alpha{}P(lime|h_{i}) P(h_{i}) $$

**Bayesian learning** simply calculates the probability of each hypothesis, given the data, and makes predictions on that basis.

So, if we pick a random bag of candy and draw a lime flavored treat, we can calculate which bag is most likely.

$$P(h_{1}|lime) = \alpha{}P(lime|h_{1}) P(h_{1}) = 0 * .1 = 0 $$
$$P(h_{2}|lime) = \alpha{}P(lime|h_{2}) P(h_{2}) = .25 * .2 = .125 $$
$$P(h_{3}|lime) = \alpha{}P(lime|h_{3}) P(h_{3}) = .5 * .4 = .2 $$
$$P(h_{4}|lime) = \alpha{}P(lime|h_{4}) P(h_{4}) = .25 * .2 = .125 $$
$$P(h_{5}|lime) = \alpha{}P(lime|h_{5}) P(h_{5}) = 1 * .1 = .1$$

Thus, the most likely hypothesis is $h_3$ at 20%.

See Figure 20.1 on page 804

In [43]:
print (nBS('l'))
print (nBS('ll'))
print (nBS('lll'))
print (nBS('llll'))

h3
h4
h5
h5


In [44]:
psource(NaiveBayesSimple)

In [45]:
{c_name: prob for c_name, prob in dist.keys()}

{'h1': 0.1, 'h2': 0.2, 'h3': 0.4, 'h4': 0.2, 'h5': 0.1}

In [46]:
{c_name: count_prob for (c_name, _), count_prob in dist.items()}

{'h1': <learning.CountingProbDist at 0x7fe9478e6f10>,
 'h2': <learning.CountingProbDist at 0x7fe9478e6e90>,
 'h3': <learning.CountingProbDist at 0x7fe9478e6e10>,
 'h4': <learning.CountingProbDist at 0x7fe94b9e1f90>,
 'h5': <learning.CountingProbDist at 0x7fe948180b10>}

### Back to the flowers

It is spring, you know.


In [50]:
dataset = iris

target_vals = dataset.values[dataset.target]
target_dist = CountingProbDist(target_vals)
attr_dists = {(gv, attr): CountingProbDist(dataset.values[attr])
              for gv in target_vals
              for attr in dataset.inputs}
for example in dataset.examples:
        targetval = example[dataset.target]
        target_dist.add(targetval)
        for attr in dataset.inputs:
            attr_dists[targetval, attr].add(example[attr])


print(target_dist['setosa'])
print(attr_dists['setosa', 0][5.0])
print(attr_dists['setosa', 0][6.0])

0.3333333333333333
0.10588235294117647
0.011764705882352941


In [49]:
attr_dists

{('setosa', 0): <learning.CountingProbDist at 0x7fe94beb6950>,
 ('setosa', 1): <learning.CountingProbDist at 0x7fe9479630d0>,
 ('setosa', 2): <learning.CountingProbDist at 0x7fe947963150>,
 ('setosa', 3): <learning.CountingProbDist at 0x7fe9479631d0>,
 ('virginica', 0): <learning.CountingProbDist at 0x7fe947963190>,
 ('virginica', 1): <learning.CountingProbDist at 0x7fe9479633d0>,
 ('virginica', 2): <learning.CountingProbDist at 0x7fe9479632d0>,
 ('virginica', 3): <learning.CountingProbDist at 0x7fe947963410>,
 ('versicolor', 0): <learning.CountingProbDist at 0x7fe947963490>,
 ('versicolor', 1): <learning.CountingProbDist at 0x7fe947963510>,
 ('versicolor', 2): <learning.CountingProbDist at 0x7fe947963310>,
 ('versicolor', 3): <learning.CountingProbDist at 0x7fe947963590>}

In [15]:
target_dist

First we found the different values for the classes (called targets here) and calculated their distribution. Next we initialized a dictionary of `CountingProbDist` objects, one for each class and feature. Finally, we iterated through the examples in the dataset and calculated the needed probabilites.

Having calculated the different probabilities, we will move on to the predicting function. It will receive as input an item and output the most likely class. Using the above formula, it will multiply the probability of the class appearing, with the probability of each feature value appearing in the class. It will return the max result.

In [51]:
def predict(example):
    def class_probability(targetval):
        return (target_dist[targetval] *
                product(attr_dists[targetval, attr][example[attr]]
                        for attr in dataset.inputs))
    return argmax(target_vals, key=class_probability)


print(predict([5, 3, 1, 0.1]))

setosa


You can view the complete code by executing the next line, which combines the above code:

In [156]:
psource(NaiveBayesDiscrete)

#### Continuous

In the implementation we use the Gaussian/Normal distribution function. To make it work, we need to find the means and standard deviations of features for each class. We make use of the `find_means_and_deviations` Dataset function. On top of that, we will also calculate the class probabilities as we did with the Discrete approach.

In [52]:
psource (DataSet)

In [61]:
means, deviations = dataset.find_means_and_deviations()

target_vals = dataset.values[dataset.target]
target_dist = CountingProbDist(target_vals)

print ('setosa:')
print('means: ' + str(means["setosa"]))
print('deviations: ' + str(deviations["setosa"]))
print ('versicolor:')
print('means: ' + str(means["versicolor"]))
print('deviations: ' + str(deviations["versicolor"]))

setosa:
means: [5.006, 3.418, 1.464, 0.244]
deviations: [0.3524896872134513, 0.38102439795469095, 0.17351115943644546, 0.10720950308167838]
versicolor:
means: [5.936, 2.77, 4.26, 1.326]
deviations: [0.5161711470638634, 0.3137983233784114, 0.46991097723995795, 0.19775268000454405]


You can see the means of the features for the "Setosa" class and the deviations for "Versicolor".

The prediction function will work similarly to the Discrete algorithm. It will multiply the probability of the class occurring with the conditional probabilities of the feature values for the class.

Since we are using the Gaussian distribution, we will input the value for each feature into the Gaussian function, together with the mean and deviation of the feature. This will return the probability of the particular feature value for the given class. We will repeat for each class and pick the max value.

In [18]:
def predict(example):
    def class_probability(targetval):
        prob = target_dist[targetval]
        for attr in dataset.inputs:
            prob *= gaussian(means[targetval][attr], deviations[targetval][attr], example[attr])
        return prob

    return argmax(target_vals, key=class_probability)


print(predict([5, 3, 1, 0.1]))

setosa


The complete code of the continuous algorithm:

In [19]:
psource(NaiveBayesContinuous)

#### Simple

The simple classifier (chosen with the argument `simple`) does not learn from a dataset, instead it takes as input a dictionary of already calculated `CountingProbDist` objects and returns a predictor function. The dictionary is in the following form: `(Class Name, Class Probability): CountingProbDist Object`.

Each class has its own probability distribution. The classifier given a list of features calculates the probability of the input for each class and returns the max. The only pre-processing work is to create dictionaries for the distribution of classes (named `targets`) and attributes/features.


This classifier is useful when you already have calculated the distributions and you need to predict future items.

### Examples

We will now use the Naive Bayes Classifier (Discrete and Continuous) to classify items:

In [161]:
nBD = NaiveBayesLearner(iris, continuous=False)
print("Discrete Classifier")
print(nBD([5, 3, 1, 0.1]))
print(nBD([6, 5, 3, 1.5]))
print(nBD([7, 3, 6.5, 2]))


nBC = NaiveBayesLearner(iris, continuous=True)
print("\nContinuous Classifier")
print(nBC([5, 3, 1, 0.1]))
print(nBC([6, 5, 3, 1.5]))
print(nBC([7, 3, 6.5, 2]))

Discrete Classifier
setosa
versicolor
versicolor

Continuous Classifier
setosa
versicolor
virginica


Notice how the Discrete Classifier misclassified the second item, while the Continuous one had no problem.

Let's now take a look at the simple classifier. First we will come up with a sample problem to solve. Say we are given three bags. Each bag contains three letters ('a', 'b' and 'c') of different quantities. We are given a string of letters and we are tasked with finding from which bag the string of letters came.

Since we know the probability distribution of the letters for each bag, we can use the naive bayes classifier to make our prediction.

In [162]:
bag1 = 'a'*50 + 'b'*30 + 'c'*15
dist1 = CountingProbDist(bag1)
bag2 = 'a'*30 + 'b'*45 + 'c'*20
dist2 = CountingProbDist(bag2)
bag3 = 'a'*20 + 'b'*20 + 'c'*35
dist3 = CountingProbDist(bag3)

Now that we have the `CountingProbDist` objects for each bag/class, we will create the dictionary. We assume that it is equally probable that we will pick from any bag.

In [163]:
dist = {('First', 0.5): dist1, ('Second', 0.3): dist2, ('Third', 0.2): dist3}
nBS = NaiveBayesLearner(dist, simple=True)

Now we can start making predictions:

In [164]:
print(nBS('aab'))        # We can handle strings
print(nBS(['b', 'b']))   # And lists!
print(nBS('ccbcc'))

First
Second
Third


The results make intuitive sense. The first bag has a high amount of 'a's, the second has a high amount of 'b's and the third has a high amount of 'c's. The classifier seems to confirm this intuition.

Note that the simple classifier doesn't distinguish between discrete and continuous values. It just takes whatever it is given. Also, the `simple` option on the `NaiveBayesLearner` overrides the `continuous` argument. `NaiveBayesLearner(d, simple=True, continuous=False)` just creates a simple classifier.